In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.patches import Circle
from matplotlib import animation
from itertools import combinations

In [ ]:
class Particle:
    def __init__(self, x, y, vx, vy, radius):

        #initialize radius, velocity, and position
        self.r = np.array((x, y))
        self.v = np.array((vx, vy))
        self.radius = radius
        
        #initialize colors based on radius of circles
        if self.radius <= 0.024:
            self.styles = {'edgecolor': 'C8', 'linewidth': 2, 'fill': None}
        if self.radius > 0.024 and self.radius <= 0.028:
            self.styles = {'edgecolor': 'C9', 'linewidth': 2, 'fill': None}
        if self.radius > 0.028 and self.radius <= 0.032:
            self.styles = {'edgecolor': 'C2', 'linewidth': 2, 'fill': None}
        if self.radius > 0.032 and self.radius <= 0.036:
            self.styles = {'edgecolor': 'C3', 'linewidth': 2, 'fill': None}
        if self.radius > 0.036 and self.radius <= 0.040:
            self.styles = {'edgecolor': 'C4', 'linewidth': 2, 'fill': None}
        if self.radius > 0.040 and self.radius <= 0.044:
            self.styles = {'edgecolor': 'C1', 'linewidth': 2, 'fill': None}
        if self.radius > 0.044 and self.radius <= 0.048:
            self.styles = {'edgecolor': 'C6', 'linewidth': 2, 'fill': None}
        if self.radius > 0.048:
            self.styles = {'edgecolor': 'C0', 'linewidth': 2, 'fill': None}
        
    # Most credit given to https://scipython.com/blog/two-dimensional-collisions/ by christian
    # For @property and setters
    @property
    def x(self):
        return self.r[0]
    @x.setter
    def x(self, value):
        self.r[0] = value
    @property
    def y(self):
        return self.r[1]
    @y.setter
    def y(self, value):
        self.r[1] = value
    @property
    def vx(self):
        return self.v[0]
    @vx.setter
    def vx(self, value):
        self.v[0] = value
    @property
    def vy(self):
        return self.v[1]
    @vy.setter
    def vy(self, value):
        self.v[1] = value

    def overlaps(self, other):
    #check if overlaps with other circles upon initilization
        return np.hypot(*(self.r - other.r)) < self.radius + other.radius

    def draw(self, ax):
    #draw in simulation
        circle = Circle(xy=self.r, radius=self.radius, **self.styles)
        ax.add_patch(circle)
        return circle

    def move(self, dt):
    #move Particle based on dt and velocity
        self.r += self.v * dt

        #make the Particles bounce off the walls
        if self.x - self.radius < 0:
            self.x = self.radius
            self.vx = -self.vx
        if self.x + self.radius > 1:
            self.x = 1-self.radius
            self.vx = -self.vx
        if self.y - self.radius < 0:
            self.y = self.radius
            self.vy = -self.vy
        if self.y + self.radius > 1:
            self.y = 1-self.radius
            self.vy = -self.vy


In [ ]:
class Simulation:
    def __init__(self, n, radius):
        self.init_particles(n, radius)

    def init_particles(self, n, radius):

        iterator = iter(radius) #radius given as list
        assert n == len(radius)


        self.n = n #number of particles 
        self.particles = []
        for i, rad in enumerate(radius):
            #try to find a random initial position for this particle.
            while True:
                #make sure x and y are inside the simulation
                x, y = rad + (1 - 2 * rad) * np.random.random(2)
                
                
                #choose random velocity
                #make it reasonable haha
                vphi = 2 * np.pi * np.random.random()
                vx = (0.1 * np.random.random() + 0.05) * np.cos(vphi) 
                vy = (0.1 * np.random.random() + 0.05) * np.sin(vphi)
                particle = Particle(x, y, vx, vy, rad)
                
                
                #check if the Particle made overlaps with already existing one(s)
                for p2 in self.particles:
                    if p2.overlaps(particle):
                        break
                else:
                    self.particles.append(particle)
                    break

    def collisions(self):
        
        def change_velocities(p1, p2):
            m1 = p1.radius**2
            m2 = p2.radius**2
            M = m1 + m2
            r1 = p1.r
            r2 = p2.r
            d = np.linalg.norm(r1 - r2)**2
            v1 = p1.v
            v2 = p2.v
            u1 = v1 - 2*m2 / M * np.dot(v1-v2, r1-r2) / d * (r1 - r2)
            u2 = v2 - 2*m1 / M * np.dot(v2-v1, r2-r1) / d * (r2 - r1)
            p1.v = u1
            p2.v = u2

        pairs = combinations(range(self.n), 2) #all the possible pairings
        for i,j in pairs:
            if self.particles[i].overlaps(self.particles[j]):
                change_velocities(self.particles[i], self.particles[j])

                
                
                
                
    # Most credit given to https://scipython.com/blog/two-dimensional-collisions/ by christian
    def advance_animation(self, dt):
        """Advance the animation by dt, returning the updated Circles list."""

        for i, p in enumerate(self.particles):
            p.move(dt)
            self.circles[i].center = p.r
        self.collisions()
        return self.circles

    def advance(self, dt):
        """Advance the animation by dt."""
        for i, p in enumerate(self.particles):
            p.move(dt)
        self.collisions()

    def init(self):
        """Initialize the Matplotlib animation."""

        self.circles = []
        for particle in self.particles:
            self.circles.append(particle.draw(self.ax))
        return self.circles

    def animate(self, i):
        """The function passed to Matplotlib's FuncAnimation routine."""

        self.advance_animation(0.01)
        return self.circles

    def do_animation(self, save=False):
        """Set up and carry out the animation of the molecular dynamics.
        To save the animation as a MP4 movie, set save=True.
        """

        fig, self.ax = plt.subplots()
        for s in ['top','bottom','left','right']:
            self.ax.spines[s].set_linewidth(2)
        self.ax.set_aspect('equal', 'box')
        self.ax.set_xlim(0, 1)
        self.ax.set_ylim(0, 1)
        self.ax.xaxis.set_ticks([])
        self.ax.yaxis.set_ticks([])
        anim = animation.FuncAnimation(fig, self.animate, init_func=self.init,
                               frames=1000, interval=2, blit=True)
        if save:
            Writer = animation.writers['ffmpeg']
            writer = Writer(fps=100, bitrate=1800)
            anim.save('collision2.mp4', writer=writer)
        else:
            plt.show()

In [ ]:
nparticles = 25
radii = np.random.random(nparticles)*0.03+0.02
sim = Simulation(nparticles, radii)
sim.do_animation(save=True)